In [ ]:
# This notebook illustrates [DALL·E mini](https://github.com/borisdayma/dalle-mini) inference pipeline.
# Just want to play? Use directly [the app](https://www.craiyon.com/).
# For more understanding of the model, refer to [the report](https://wandb.ai/dalle-mini/dalle-mini/reports/DALL-E-mini--Vmlldzo4NjIxODA).

# Required only for colab environments + GPU
!pip install flax==0.6.3 orbax==0.0.23 transformers==4.25.1 chex==0.1.6 orbax-checkpoint==0.0.0
!pip install jax==0.3.25 jaxlib==0.3.25 -f https://storage.googleapis.com/jax-releases/jax_cuda_releases.html

# Install required libraries
!pip install -q dalle-mini
!pip install -q git+https://github.com/patil-suraj/vqgan-jax.git

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 197.4/197.4 kB 5.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.6/66.6 kB 9.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.8/5.8 MB 66.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 87.9/87.9 kB 13.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 103.5 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of optax to determine which version is compatible with other requirements. This could take a while.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 209.9/209.9 kB 27.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 209.5/209.5 kB 28.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 197.2/197.2 kB 29.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 200.0/200.0 kB 27.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 154.1/154.1 kB 22.2 MB/s eta 0:00:00
  Attempting uninstall: tokenizers
    Fo

In [ ]:
# Downgrade CUDA to 11.0.2 to work with jax 0.3.25 version
!wget https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1604/x86_64/cuda-ubuntu1604.pin
!sudo mv cuda-ubuntu1604.pin /etc/apt/preferences.d/cuda-repository-pin-600
!wget http://developer.download.nvidia.com/compute/cuda/11.0.2/local_installers/cuda-repo-ubuntu1604-11-0-local_11.0.2-450.51.05-1_amd64.deb
!sudo dpkg -i cuda-repo-ubuntu1604-11-0-local_11.0.2-450.51.05-1_amd64.deb
!sudo apt-key add /var/cuda-repo-ubuntu1604-11-0-local/7fa2af80.pub
!sudo apt-get update
!sudo apt-get -y install cuda-11-0 # INPUT: 94 and 1 for turkish, 32
#!export CUDA_PATH=/usr/local/cuda-11.0/
#!nvcc --version

--2024-05-19 23:01:28--  https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1604/x86_64/cuda-ubuntu1604.pin
Resolving developer.download.nvidia.com (developer.download.nvidia.com)... 152.199.39.144
Connecting to developer.download.nvidia.com (developer.download.nvidia.com)|152.199.39.144|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 190 [application/octet-stream]
Saving to: ‘cuda-ubuntu1604.pin’

cuda-ubuntu1604.pin 100%[===================>]     190  --.-KB/s    in 0s      

2024-05-19 23:01:28 (6.58 MB/s) - ‘cuda-ubuntu1604.pin’ saved [190/190]

--2024-05-19 23:01:28--  http://developer.download.nvidia.com/compute/cuda/11.0.2/local_installers/cuda-repo-ubuntu1604-11-0-local_11.0.2-450.51.05-1_amd64.deb
Resolving developer.download.nvidia.com (developer.download.nvidia.com)... 152.199.39.144
Connecting to developer.download.nvidia.com (developer.download.nvidia.com)|152.199.39.144|:80... connected.
HTTP request sent, awaiting response... 301 Mov

In [ ]:
# Model references

# dalle-mega
DALLE_MODEL = "dalle-mini/dalle-mini/mega-1-fp16:latest"  # can be wandb artifact or 🤗 Hub or local folder or google bucket
DALLE_COMMIT_ID = None # Why none?

# if the notebook crashes too often you can use dalle-mini instead by uncommenting below line
# DALLE_MODEL = "dalle-mini/dalle-mini/mini-1:v0"

# VQGAN model
VQGAN_REPO = "dalle-mini/vqgan_imagenet_f16_16384"
VQGAN_COMMIT_ID = "e93a26e7707683d349bf5d5c41c5b0ef69b677a9"

import jax
import jax.numpy as jnp

# check how many devices are available
jax.local_device_count()

1

In [ ]:
# Load models & tokenizer
from dalle_mini import DalleBart, DalleBartProcessor
from vqgan_jax.modeling_flax_vqgan import VQModel
from transformers import CLIPProcessor, FlaxCLIPModel

# Load dalle-mini
model, params = DalleBart.from_pretrained(
    DALLE_MODEL, revision=DALLE_COMMIT_ID, dtype=jnp.float16, _do_init=False
)

# Load VQGAN
vqgan, vqgan_params = VQModel.from_pretrained(
    VQGAN_REPO, revision=VQGAN_COMMIT_ID, _do_init=False
)

'''
wandb.ai api key:
9e3ef9b05655a6c83d987cff913161219b65b12b
'''

wandb: Downloading large artifact mega-1-fp16:latest, 4938.53MB. 7 files... 
wandb:   7 of 7 files downloaded.  
Done. 0:0:11.2
Some of the weights of DalleBart were initialized in float16 precision from the model checkpoint at /tmp/tmprpz3bunq:
[('lm_head', 'kernel'), ('model', 'decoder', 'embed_positions', 'embedding'), ('model', 'decoder', 'embed_tokens', 'embedding'), ('model', 'decoder', 'final_ln', 'bias'), ('model', 'decoder', 'layernorm_embedding', 'bias'), ('model', 'decoder', 'layernorm_embedding', 'scale'), ('model', 'decoder', 'layers', 'FlaxBartDecoderLayers', 'FlaxBartAttention_0', 'k_proj', 'kernel'), ('model', 'decoder', 'layers', 'FlaxBartDecoderLayers', 'FlaxBartAttention_0', 'out_proj', 'kernel'), ('model', 'decoder', 'layers', 'FlaxBartDecoderLayers', 'FlaxBartAttention_0', 'q_proj', 'kernel'), ('model', 'decoder', 'layers', 'FlaxBartDecoderLayers', 'FlaxBartAttention_0', 'v_proj', 'kernel'), ('model', 'decoder', 'layers', 'FlaxBartDecoderLayers', 'FlaxBartAttention

'\nwandb.ai api key:\n9e3ef9b05655a6c83d987cff913161219b65b12b\n'

In [ ]:
# Model parameters are replicated on each device for faster inference.
from flax.jax_utils import replicate
params = replicate(params)
vqgan_params = replicate(vqgan_params)
# Model functions are compiled and parallelized to take advantage of multiple devices.
from functools import partial
# model inference
@partial(jax.pmap, axis_name="batch", static_broadcasted_argnums=(3, 4, 5, 6))
def p_generate(
    tokenized_prompt, key, params, top_k, top_p, temperature, condition_scale
):
    return model.generate(
        **tokenized_prompt,
        prng_key=key,
        params=params,
        top_k=top_k,
        top_p=top_p,
        temperature=temperature,
        condition_scale=condition_scale,
    )
# decode image
@partial(jax.pmap, axis_name="batch")
def p_decode(indices, params):
    return vqgan.decode_code(indices, params=params)

from dalle_mini import DalleBartProcessor
processor = DalleBartProcessor.from_pretrained(DALLE_MODEL, revision=DALLE_COMMIT_ID)

wandb: Downloading large artifact mega-1-fp16:latest, 4938.53MB. 7 files... 
wandb:   7 of 7 files downloaded.  
Done. 0:0:12.2
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [ ]:
# GENERATE IMAGES
# We generate images using dalle-mini model and decode them with the VQGAN.
from flax.training.common_utils import shard_prng_key
import numpy as np
from PIL import Image
from tqdm.notebook import trange
import os

# generate images
images = []
def generate_image(prompt, key, current_time, index = None,
                   n_predictions = 1,
                   gen_top_k = None,
                   gen_top_p = None,
                   temperature = None,
                   cond_scale = 10.0):

  # We can customize generation parameters (see https://huggingface.co/blog/how-to-generate)
  tokenized_prompts = processor(prompt)
  tokenized_prompt = replicate(tokenized_prompts)

  for i in trange(max(n_predictions // jax.device_count(), 1)):
      # get a new key
      key, subkey = jax.random.split(key)
      # generate images
      encoded_images = p_generate(
          tokenized_prompt,
          shard_prng_key(subkey),
          params,
          gen_top_k,
          gen_top_p,
          temperature,
          cond_scale,
      )
      # remove BOS
      encoded_images = encoded_images.sequences[..., 1:]
      # decode images
      decoded_images = p_decode(encoded_images, vqgan_params)
      decoded_images = decoded_images.clip(0.0, 1.0).reshape((-1, 256, 256, 3))
      for decoded_img in decoded_images:
          img = Image.fromarray(np.asarray(decoded_img * 255, dtype=np.uint8))
          #img.save(f'inference/{current_time}/{caption}.png')
          # save figure
          if index == None:
              caption = prompt[0]
              try:
                  img.save(f'inference/{current_time}/{caption}.png') # save image
                  #PIL.Image.fromarray(generated_image.to(device).numpy(), 'RGB').save(f'inference/{current_time}/{caption}.png') # save image
                  #plt.savefig(f'inference/{current_time}/{caption}.png')
              except:
                  try:
                      os.mkdir(f'inference/{current_time}')
                      img.save(f'inference/{current_time}/{caption}.png') # save image
                      #plt.savefig(f'inference/{current_time}/{caption}.png')
                      #PIL.Image.fromarray(generated_image.to(device).numpy(), 'RGB').save(f'inference/{current_time}/{caption}.png') # save image
                  except:
                      os.mkdir('./inference')
                      os.mkdir(f'inference/{current_time}')
                      img.save(f'inference/{current_time}/{caption}.png') # save image
                      #plt.savefig(f'inference/{current_time}/{caption}.png')
                      #PIL.Image.fromarray(generated_image.to(device).numpy(), 'RGB').save(f'inference/{current_time}/{caption}.png') # save image
          elif index != None:
                  try:
                      img.save(f'inference/{current_time}/{index:05d}.png') # save image
                      #PIL.Image.fromarray(generated_image.to(device).numpy(), 'RGB').save(f'inference/{current_time}/{caption}.png') # save image
                      #plt.savefig(f'inference/{current_time}/{caption}.png')
                  except:
                      try:
                          os.mkdir(f'inference/{current_time}')
                          img.save(f'inference/{current_time}/{index:05d}.png') # save image
                          #plt.savefig(f'inference/{current_time}/{caption}.png')
                          #PIL.Image.fromarray(generated_image.to(device).numpy(), 'RGB').save(f'inference/{current_time}/{caption}.png') # save image
                      except:
                          os.mkdir('./inference')
                          os.mkdir(f'inference/{current_time}')
                          img.save(f'inference/{current_time}/{index:05d}.png') # save image
                          #plt.savefig(f'inference/{current_time}/{caption}.png')
                          #PIL.Image.fromarray(generated_image.to(device).numpy(), 'RGB').save(f'inference/{current_time}/{caption}.png') # save image

          #images.append(img)
          #display(img)
          #print()


In [ ]:
# Download dataset:
!gdown -O dataset.zip https://drive.google.com/uc?id=1JtRIbZDuZlBEA6vp870eW3ei0r32uYqF
# https://drive.google.com/file/d/1JtRIbZDuZlBEA6vp870eW3ei0r32uYqF/view?usp=sharing
!unzip -q dataset.zip

Downloading...
From (original): https://drive.google.com/uc?id=1JtRIbZDuZlBEA6vp870eW3ei0r32uYqF
From (redirected): https://drive.google.com/uc?id=1JtRIbZDuZlBEA6vp870eW3ei0r32uYqF&confirm=t&uuid=09ce2125-44df-4b1d-b1d3-fa7bfd5cdbd9
To: /content/dataset.zip
100% 852M/852M [00:24<00:00, 34.5MB/s]


In [ ]:
# Read dataset/image_captions_cleaned captions with pandas:
import pandas as pd
dtype_dict = {'name': str, 'caption': str}
df2 = pd.read_csv('dataset/image_captions_cleaned.txt', sep=",", header=0, dtype=dtype_dict)
saved_captions = df2['caption'].tolist()
len(saved_captions), type(saved_captions)

(2048, list)

In [ ]:
# 2048 INFERENCE IMAGES SAVING FOR EVALUATION METRICS
# Multiple captions in loop
from datetime import datetime
from tqdm.auto import tqdm
import random
current_time = datetime.now().strftime("%Y-%m-%d_%H-%M-%S")
index = 0
for idx in tqdm(saved_captions):
    # Keys are passed to the model on each device to generate unique inference per device.
    seed = random.randint(0, 2**32 - 1)
    key = jax.random.PRNGKey(seed)
    index += 1
    generate_image([idx], key, current_time, index = index)
    #Inference(idx, current_time, save_fig = True, show_pic = False, index = index)

import os
print(str(len(os.listdir('/content/inference/'+current_time)))+' images are saved.')

  0%|          | 0/2048 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

2048 images are saved.


In [19]:
current_time

'2024-05-19_23-43-02'

In [20]:
!cd inference && zip -r dalle-mini-vqgan.zip 2024-05-19_23-43-02/
# To save inference output zip to google drive
from google.colab import drive
drive.mount('/content/drive')
!cp -r /content/inference/dalle-mini-vqgan.zip /content/drive/MyDrive/dalle-mini-vqgan.zip

  adding: 2024-05-19_23-43-02/ (stored 0%)
  adding: 2024-05-19_23-43-02/00028.png (deflated 0%)
  adding: 2024-05-19_23-43-02/01195.png (deflated 0%)
  adding: 2024-05-19_23-43-02/01462.png (deflated 0%)
  adding: 2024-05-19_23-43-02/01921.png (deflated 0%)
  adding: 2024-05-19_23-43-02/00456.png (deflated 0%)
  adding: 2024-05-19_23-43-02/01895.png (deflated 0%)
  adding: 2024-05-19_23-43-02/00757.png (deflated 0%)
  adding: 2024-05-19_23-43-02/00500.png (deflated 0%)
  adding: 2024-05-19_23-43-02/00813.png (deflated 0%)
  adding: 2024-05-19_23-43-02/00304.png (deflated 0%)
  adding: 2024-05-19_23-43-02/02032.png (deflated 0%)
  adding: 2024-05-19_23-43-02/00778.png (deflated 0%)
  adding: 2024-05-19_23-43-02/00146.png (deflated 0%)
  adding: 2024-05-19_23-43-02/00683.png (deflated 0%)
  adding: 2024-05-19_23-43-02/00242.png (deflated 0%)
  adding: 2024-05-19_23-43-02/01394.png (deflated 0%)
  adding: 2024-05-19_23-43-02/00420.png (deflated 0%)
  adding: 2024-05-19_23-43-02/01214.png